## LightGBM + FT_transformer

In [1]:
import numpy as np
import pandas as pd
from copy import deepcopy
import matplotlib.pyplot as plt
import seaborn as sns
import tqdm
import gc
import lightgbm as lgb
import os
import warnings
import torch

warnings.filterwarnings("ignore")

In [2]:
train = pd.read_csv("Lynn/p14_train_fe_hsp.csv")
train['istrain'] = 1
test = pd.read_csv("Lynn/p14_test_fe_hsp.csv")
test['istrain'] = 0
df = pd.concat([train, test]).reset_index(drop=True)

X_name = df.columns.tolist()[:-7]
Y_name = [f'property {i}' for i in range(1,7)]

poolx = df[X_name].copy(deep=True)
pooly = df[Y_name].copy(deep=True)

X = poolx.iloc[df[df['istrain']==1].index, :]
Y = pooly.iloc[df[df['istrain']==1].index, :]

X_test = poolx.iloc[df[df['istrain']==0].index, :].reset_index(drop=True)
Y_test = pooly.iloc[df[df['istrain']==0].index, :].reset_index(drop=True)

pred = torch.zeros((X_test.shape[0], 6))
print(X.shape, X_test.shape)


(1372, 145) (588, 145)


In [3]:
X.shape, X_test.shape

((1372, 145), (588, 145))

In [4]:
models = os.listdir('final_lgb_models_3fold')
lgb_X = []
lgb_X_test = []
gbm_leaf_value = {}
columns = []
for model in models:
    gbm = lgb.Booster(model_file='final_lgb_models_3fold/'+ model)
    model_name =model.split('.')[0]
    gbm_leaf_value[model_name] = {}
    for i in range(gbm.num_trees()):
        gbm_leaf_value[model_name][i] = {}
        columns.append(model_name + '_' + str(i))
        for j in range(31):
            try:
                gbm_leaf_value[model_name][i][j] = gbm.get_leaf_output(i, j)
            except:
                continue
    lgb_X.append(gbm.predict(X, pred_leaf = True))
    lgb_X_test.append(gbm.predict(X_test, pred_leaf = True))

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: leaf_idx >= 0 && leaf_idx < models_[tree_idx]->num_leaves() at /__w/1/s/python-package/compile/src/boosting/gbdt.h, line 380 .

[LightGBM] [Fatal] Check failed: l

In [5]:
lgb_X = [pd.DataFrame(i) for i in lgb_X]
lgb_X_test = [pd.DataFrame(i) for i in lgb_X_test]

all_lgb_X = pd.concat(lgb_X, axis=1)
all_lgb_X.columns = columns

all_lgb_X_test = pd.concat(lgb_X_test, axis=1)
all_lgb_X_test.columns = columns

In [6]:
all_lgb_X

property_1_fold3_model_0  property_1_fold3_model_1  \
0                            3                         3   
1                            0                         0   
2                            0                         0   
3                            0                         0   
4                            2                         2   
...                        ...                       ...   
1367                         2                         2   
1368                         2                         2   
1369                         0                         0   
1370                         0                         0   
1371                         3                         3   

      property_1_fold3_model_2  property_1_fold3_model_3  \
0                            3                         0   
1                            0                         3   
2                            0                         3   
3                            0                         3   
4                            2                         2   
...                        ...                       ...   
1367                         2                         2   
1368                         2                         2   
1369                         0                         3   
1370                         0                         3   
1371                         3                         0   

      property_1_fold3_model_4  property_1_fold3_model_5  \
0                            2                         2   
1                            4                         0   
2                            4                         0   
3                            4                         0   
4                            0                         1   
...                        ...                       ...   
1367                         0                         2   
1368                         3                         2   
1369                         4                         0   
1370                         4                         0   
1371                         2                         2   

      property_1_fold3_model_6  property_1_fold3_model_7  \
0                            1                         0   
1                            6                         3   
2                            6                         4   
3                            6                         4   
4                            0                         0   
...                        ...                       ...   
1367                         4                         2   
1368                         2                         2   
1369                         6                         4   
1370                         6                         4   
1371                         1                         0   

      property_1_fold3_model_8  property_1_fold3_model_9  ...  \
0                            2                         2  ...   
1                            0                         0  ...   
2                            0                         0  ...   
3                            0                         0  ...   
4                            1                         1  ...   
...                        ...                       ...  ...   
1367                         2                         2  ...   
1368                         2                         2  ...   
1369                         0                         0  ...   
1370                         0                         0  ...   
1371                         2                         2  ...   

      property_6_fold3_model_100  property_6_fold3_model_101  \
0                              5                           0   
1                              7                           5   
2                              7                           0   
3                              6                           4   
4                    

In [7]:
new_df = {}
for name in columns:
    col_leaf_index = all_lgb_X[name].values.tolist()
    model_name, tree_name = name[:22], int(name[23:])
    col_leaf_value = [gbm_leaf_value[model_name][tree_name][i] for i in col_leaf_index]
    new_df[name] = col_leaf_value

new_df = pd.DataFrame(new_df)

In [8]:
new_df_test = {}
for name in columns:
    col_leaf_index = all_lgb_X_test[name].values.tolist()
    model_name, tree_name = name[:22], int(name[23:])
    col_leaf_value = [gbm_leaf_value[model_name][tree_name][i] for i in col_leaf_index]
    new_df_test[name] = col_leaf_value
    
new_df_test = pd.DataFrame(new_df_test)

In [9]:
new_df_test

property_1_fold3_model_0  property_1_fold3_model_1  \
0                    0.137971                 -0.002392   
1                    0.137971                 -0.002392   
2                    0.137971                 -0.002392   
3                    0.137971                 -0.002392   
4                    0.137971                 -0.002392   
..                        ...                       ...   
583                  0.140288                 -0.000098   
584                  0.137971                 -0.002392   
585                  0.137971                 -0.002392   
586                  0.190397                  0.049510   
587                  0.137971                 -0.002392   

     property_1_fold3_model_2  property_1_fold3_model_3  \
0                   -0.002368                 -0.002321   
1                   -0.002368                 -0.002321   
2                   -0.002368                 -0.002321   
3                   -0.002368                 -0.002321   
4                   -0.002368                 -0.002321   
..                        ...                       ...   
583                 -0.000097                  0.000014   
584                 -0.002368                 -0.002321   
585                 -0.002368                 -0.002321   
586                  0.049015                  0.048525   
587                 -0.002368                 -0.002321   

     property_1_fold3_model_4  property_1_fold3_model_5  \
0                   -0.002257                 -0.002307   
1                   -0.002257                 -0.002307   
2                   -0.002257                 -0.002307   
3                   -0.002257                 -0.002307   
4                   -0.002257                 -0.002307   
..                        ...                       ...   
583                  0.003665                  0.002106   
584                 -0.002257                 -0.002307   
585                 -0.002257                 -0.002307   
586                  0.015339                  0.024317   
587                 -0.002257                 -0.002307   

     property_1_fold3_model_6  property_1_fold3_model_7  \
0                   -0.002301                 -0.002258   
1                   -0.002301                 -0.002258   
2                   -0.002301                 -0.002258   
3                   -0.002301                  0.016253   
4                   -0.002301                 -0.002258   
..                        ...                       ...   
583                  0.002708                  0.006679   
584                 -0.002301                 -0.002258   
585                 -0.002301                 -0.002258   
586                  0.007339                  0.016253   
587                 -0.002301                 -0.002258   

     property_1_fold3_model_8  property_1_fold3_model_9  ...  \
0                   -0.002236                 -0.002213  ...   
1                   -0.002236                 -0.002213  ...   
2                   -0.002236                 -0.002213  ...   
3                   -0.002236                 -0.002213  ...   
4                   -0.002236                 -0.002213  ...   
..                        ...                       ...  ...   
583                  0.002021                  0.002072  ...   
584                 -0.002236                 -0.002213  ...   
585                 -0.002236                 -0.002213  ...   
586                  0.023756                  0.023519  ...   
587                 -0.002236                 -0.002213  ...   

     property_6_fold3_model_100  property_6_fold3_model_101  \
0                     -0.002446                   -0.001780   
1                      0.004162                   -0.001780   
2                     -0.002446                   -0.001780   
3                      0.004162                    0.005257   
4                     -0.005358                   -0.001780   
..                    

In [10]:
#concatenate origin feature 
train = pd.read_csv("Lynn/p14_train_fe_hsp.csv")
test = pd.read_csv("Lynn/p14_test_fe_hsp.csv")
X_name = df.columns.tolist()[:-7]
ori_train = train[X_name]
ori_test = test[X_name]

X = new_df.join(ori_train)
X_test = new_df_test.join(ori_test)
X.shape, X_test.shape

((1372, 1709), (588, 1709))

In [11]:
os.environ["CUDA_DEVICE_ORDER"] = 'PCI_BUS_ID'
os.environ["CUDA_VISIBLE_DEVICES"] = '2'

device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [12]:
from sklearn.model_selection import KFold
from utils.data import MyDataset
from torch.utils.data import DataLoader
from utils.trainer import trainer
from models.ft_transformer import FT_Transformer

os.environ["CUDA_DEVICE_ORDER"] = 'PCI_BUS_ID'
os.environ["CUDA_VISIBLE_DEVICES"] = '1'

device = 'cuda' if torch.cuda.is_available() else 'cpu'

kf = KFold(n_splits=5, random_state=2022, shuffle=True)

oof_train = torch.zeros((X.shape[0], 6))
oof_real_train = torch.zeros((X.shape[0], 6))

use_cat=False

pred = torch.zeros((X_test.shape[0], 6))


for now_fold, (trn_idx, val_idx) in enumerate(kf.split(X, Y)):
    print(f"Fold: {now_fold}")
    X_train, X_val = np.array(X.iloc[trn_idx]), np.array(X.iloc[val_idx])
    y_train, y_val = np.array(Y.iloc[trn_idx]), np.array(Y.iloc[val_idx])
    
    X_train, X_val = torch.tensor(X_train).float(), torch.tensor(X_val).float()
    y_train, y_val = torch.tensor(y_train).float(), torch.tensor(y_val).float()
    
    train_dataset = MyDataset(X_train, y_train)
    valid_dataset = MyDataset(X_val, y_val)
    
    train_dataloader = DataLoader(train_dataset, batch_size=32, shuffle=True)
    valid_dataloader = DataLoader(valid_dataset, batch_size=32, shuffle=True)
    
    
    model = FT_Transformer(in_dim=X.shape[1], d_numerical=256, categories=None, token_bias=True, n_layers=3, d_token=256, n_heads=4,
                           d_ffn_factor=3.0, attention_dropout=0.2, ffn_dropout=0.2,residual_dropout=0.2)
                      
    final_model = trainer(model, train_dataloader, valid_dataloader, device, max_epochs=2000, early_stop=20, use_cat=use_cat)
    final_model = final_model.to('cpu')
    if use_cat:
        oof_train[val_idx]= final_model(X_val[:,:-12], X_val[:,-12:].int() ).detach()
        pred += final_model(
            torch.Tensor(X_test.values[:,:-12]), torch.Tensor(X_test.values[:,-12:]).int()
                            ).detach() / 5
    else:
        oof_train[val_idx] = final_model(X_val, None).detach()
        oof_real_train[trn_idx] += final_model(X_train, None).detach() / 4
        pred += final_model(torch.Tensor(X_test.values).float(), None).detach() /5

Fold: 0
epoch:    1 | train_loss: 33.3358 | train_mae: 0.5685 | train_r2: 0.0093 | train_rmse: 0.9658 | train_pccs: 0.2201
epoch:    1 | valid_loss: 28.5434 | valid_mae: 0.4158 | valid_r2: 0.4132 | valid_rmse: 1.3328 | valid_pccs: 0.5243
epoch:    2 | train_loss: 20.5970 | train_mae: 0.2855 | train_r2: 0.4768 | train_rmse: 0.6436 | train_pccs: 0.5717
epoch:    2 | valid_loss: 28.1511 | valid_mae: 0.2998 | valid_r2: 0.5106 | valid_rmse: 1.2491 | valid_pccs: 0.5985
epoch:    3 | train_loss: 18.3062 | train_mae: 0.2477 | train_r2: 0.5512 | train_rmse: 0.5961 | train_pccs: 0.6509
epoch:    3 | valid_loss: 26.9462 | valid_mae: 0.3118 | valid_r2: 0.5495 | valid_rmse: 1.2186 | valid_pccs: 0.6444
epoch:    4 | train_loss: 16.9553 | train_mae: 0.2247 | train_r2: 0.5940 | train_rmse: 0.5590 | train_pccs: 0.6876
epoch:    4 | valid_loss: 26.5143 | valid_mae: 0.2525 | valid_r2: 0.5912 | valid_rmse: 1.1608 | valid_pccs: 0.6758
epoch:    5 | train_loss: 16.1932 | train_mae: 0.2027 | train_r2: 0.6185

In [17]:
from scipy.stats import pearsonr
from sklearn.metrics import mean_absolute_error, r2_score
print("train")

for i in range(Y.shape[1]):
    mae = mean_absolute_error(Y.iloc[:,i], oof_real_train[:,i])
    r2 = r2_score(Y.iloc[:,i], oof_real_train[:,i])
    rmse = np.sqrt(((Y.iloc[:, i] - np.array(oof_real_train[:,i])) ** 2).mean())
    pccs = pearsonr(Y.iloc[:, i], oof_real_train[:,i])[0]
    mae, r2, rmse, pccs = np.around([mae, r2, rmse, pccs], decimals=4)
    print(f'property{i+1}: mae:{mae}, rmse:{rmse}, r2:{r2}, pccs:{pccs}')

print("valid")

for i in range(Y.shape[1]):
    mae = mean_absolute_error(Y.iloc[:,i], oof_train[:,i])
    r2 = r2_score(Y.iloc[:,i], oof_train[:,i])
    rmse = np.sqrt(((Y.iloc[:, i] - np.array(oof_train[:,i])) ** 2).mean())
    pccs = pearsonr(Y.iloc[:, i], oof_train[:,i])[0]
    mae, r2, rmse, pccs = np.around([mae, r2, rmse, pccs], decimals=4)
    print(f'property{i+1}: mae:{mae}, rmse:{rmse}, r2:{r2}, pccs:{pccs}')

print("test")
for i in range(Y_test.shape[1]):
    mae = mean_absolute_error(Y_test.iloc[:,i], pred[:,i])
    r2 = r2_score(Y_test.iloc[:,i], pred[:,i])
    rmse = np.sqrt(((Y_test.iloc[:, i] - np.array(pred[:,i])) ** 2).mean())
    pccs = pearsonr(Y_test.iloc[:, i], pred[:,i])[0]
    mae, r2, rmse, pccs = np.around([mae, r2, rmse, pccs], decimals=4)
    print(f'property{i+1}: mae:{mae}, rmse:{rmse}, r2:{r2}, pccs:{pccs}')

train
property1: mae:0.1446, rmse:1.4726, r2:0.3081, pccs:0.6519
property2: mae:0.068, rmse:0.1098, r2:0.9845, pccs:0.9923
property3: mae:0.0365, rmse:0.0605, r2:0.9944, pccs:0.9973
property4: mae:0.0545, rmse:0.0806, r2:0.9927, pccs:0.9964
property5: mae:0.2056, rmse:1.5823, r2:0.064, pccs:0.364
property6: mae:0.3673, rmse:0.5147, r2:0.7174, pccs:0.8495
valid
property1: mae:0.1889, rmse:1.5416, r2:0.2417, pccs:0.5376
property2: mae:0.0797, rmse:0.1279, r2:0.979, pccs:0.9895
property3: mae:0.0543, rmse:0.0903, r2:0.9875, pccs:0.9938
property4: mae:0.0712, rmse:0.1125, r2:0.9858, pccs:0.9929
property5: mae:0.2358, rmse:1.6253, r2:0.0123, pccs:0.1123
property6: mae:0.4167, rmse:0.5875, r2:0.6317, pccs:0.7949
test
property1: mae:0.072, rmse:0.1979, r2:0.6641, pccs:0.8774
property2: mae:0.0652, rmse:0.1015, r2:0.9877, pccs:0.994
property3: mae:0.0353, rmse:0.0624, r2:0.9932, pccs:0.9966
property4: mae:0.0496, rmse:0.0752, r2:0.9939, pccs:0.997
property5: mae:0.109, rmse:0.4916, r2:0.1739, 